# aq_udb

## Overview
`aq_udb` command let users interact with UDB (User Database). It is distributed, hash-based, in memory database. 
It is designed to process vast amount of data in a computing cluster, where each node is responsible for unique set of primary keys in the database. 

This allows users to perform much more complex analysis and queries than `aq_pp` command could alone, on larger datasets.

`aq_udb` is used to perform data cleaning and transforming with UDB once the database is created. 

### Components of UDB
* **Database:** User database, that contains one or more of the following components
* **Table:** similar to TABLE in MySQL, with schema that is a variant of column spec
* **Vector:** a single record of data, you can specify [attributes](http://auriq.com/documentation/source/reference/tables/index.html#attributes) with each column, and stream data within it to calculate values.
* **Variable:** Variable to store value

**Note:** Keep in mind that the definitions of these components above are immutable once created. Users can only change data / values inside it with command. 

## Data and Database setup

We'll be using [amazon customer review dataset](https://s3.amazonaws.com/amazon-reviews-pds/readme.html)'s international market's data, namely Japan and UK's reviews.

**Database**<br>
Followings are some important info about the database we'll create.
* Database: `amazon`
* Table: `reviews`
> Column spec for table: `S:marketplace I:customer_id S:review_id S:product_id I:product_parent S:product_title S,pkey:product_category I:star_rating I:helpful_votes I:total_votes S:vine S:verified_purchase S:review_headline S:review_body S:review_date`
* Primary key (column): `product_category`

## Contents
In this notebook, first we'll go though the general steps of managing database, then go over examples for each option of `aq_udb` command.

### Manage UDB

#### [Preparing Database](#prep_db)


#### [Checking Database State](#check_db)

#### [Clean Up Database](#clean_db)


### [aq_udb](#aq_udb_option)<br>

As a example notebook, some of the options will be covered here, but not all. For the list of available options, please refer to `man aq_udb` command.

* [`-exp`](#exp) - export data 
* [`-top [Start:]Num`](#top) - limit the output result to `Num` of records from top of the DB
* [`-last [Start:]Num`](#last) - same as above, but from buttom
* [`-lim_rec Num`](#lim_rec) - output `Num` of records
* [`-lim_key Num`](#lim_key) - output `Num` of unique keys and associated records only
* [`-key_rec Num`](#key_rec) - output `Num` of records per unique key
 of the dB 
* [`-sort`](#sort) - sort output data
* [`-ord`](#ord) - sort keys in DB, or records in table internally
* [`-shf`](#shf) - shuffle keys or records in DB internally
* [`-cnt`](#cnt) - count unique primary keys in DB
* [`-eval`](#eval) - same as `aq_pp`'s option
* [`-filt`](#filt) - same as `aq_pp`'s option
* [`-var`](#var) - assign value to predefined variable


<a id='prep_db'></a>
### Preparing Database
In this section we'll cover steps to prepare udb for use, for the first time.
This includes steps below
* selecting datastore and creating data category
* taking a look at data, and getting column spec
* creating database schema
* starting database server

Let's start with preparing the data we'll use.

**Prepare Data**

In [8]:
# select datastore, which is s3 bucket
ess select essentia-playground

# display the directory structures and files stored
ess ls /tsv/ | head -n 10

# create data category
ess category add amazon \
 '/tsv/amazon_reviews_multilingual_UK_v1_00.tsv.gz /tsv/amazon_reviews_multilingual_JP_v1_00.tsv.gz'
 
# get info about the category
ess summary amazon | head -n 10

 230M Nov 12 23:31    /tsv/amazon_reviews_multilingual_DE_v1_00.tsv.gz
  67M Nov 12 23:31    /tsv/amazon_reviews_multilingual_FR_v1_00.tsv.gz
  90M Nov 12 23:31    /tsv/amazon_reviews_multilingual_JP_v1_00.tsv.gz
 333M Nov 12 23:31    /tsv/amazon_reviews_multilingual_UK_v1_00.tsv.gz
 1.4G Nov 12 23:31    /tsv/amazon_reviews_multilingual_US_v1_00.tsv.gz
 618M Nov 12 23:31    /tsv/amazon_reviews_us_Apparel_v1_00.tsv.gz
 555M Nov 12 23:31    /tsv/amazon_reviews_us_Automotive_v1_00.tsv.gz
 340M Nov 12 23:31    /tsv/amazon_reviews_us_Baby_v1_00.tsv.gz
 871M Nov 12 23:31    /tsv/amazon_reviews_us_Beauty_v1_00.tsv.gz
 2.6G Nov 12 23:31    /tsv/amazon_reviews_us_Books_v1_00.tsv.gz
2019-11-15 19:43:45 ip-10-10-1-118 ess[9162]: !!!Warning!!! Category amazon already defined. Ignoring command.
Name:        amazon
Pattern:     tsv/amazon_reviews_multilingual_JP_v1_00.tsv.gz /tsv/amazon_reviews_multilingual_UK_v1_00.tsv.gz
Exclude:     None
Date Format: auto
Date Regex:  
Archive:     
Delimiter:   

Now we have some information that we need about the data in order to define database schema. We have column spec. 
Let's go ahead and create database and table now.
<a id='db_creation'></a>
**Database Creation**<br>
We'll create 
* database named `amazon` 
* table `reviews` with 
    * schema - column spec of the data from the data category.
    > When creating schema, we need to specify primary key column, much like SQL database. Here is the schema.
    `S:marketplace I,pkey:customer_id S:review_id S:product_id I:product_parent S:product_title S:product_category I:star_rating I:helpful_votes I:total_votes S:vine S:verified_purchase S:review_headline S:review_body S:review_date`
    * Note the `I,pkey:customer_id`, `pkey` specify that this column is the primary key of the table.
    
We can use  `ess create {}` where you can specify entity to create and pass in name of the entity.

After that, we'll start database server.

In [85]:
# delete database, schema and data if already exist
ess server reset 
# creating database named amazon
ess create database amazon
# creating table named reviews, with the schema
ess create table reviews S:marketplace I:customer_id S:review_id S:product_id I:product_parent S:product_title S,pkey:product_category I:star_rating I:helpful_votes I:total_votes S:vine S:verified_purchase S:review_headline S:review_body S:review_date
# create variable
ess create variable star_sum 0
# start the db server
ess udbd start

2019-11-15 23:08:13 ip-10-10-1-118 ess[11709]: ***Error*** need more than 0 values to unpack
ip-10-10-1-118: Starting udbd-10010.
ip-10-10-1-118: udbd-10010 (11780) started.


<a id='db_population'></a>
**Populate it with Data**<br>

Now we'll fill up the database with the review dataset, using essentia's stream and `aq_pp` command. Note that **`-imp` option is used to direct the output into the database**.

In [86]:
ess stream amazon "*" "*" 'aq_pp -f,+1,tsv,eok - -d %cols -imp amazon:reviews' 

2019-11-15 23:09:06 ip-10-10-1-118 ess[11802]: !!!Warning!!! Multiple warnings.  See task.log for more details


Using `aq_udb` with [`-exp`](#exp) command, we can see that the data is inside of the database. 

In [36]:
ess exec "aq_udb -exp amazon:reviews -lim_rec 30"

"marketplace","customer_id","review_id","product_id","product_parent","product_title","product_category","star_rating","helpful_votes","total_votes","vine","verified_purchase","review_headline","review_body","review_date"
"UK",10349,"R2YVNBBMXD8KVJ","B00MWK7BWG",307651059,"My Favourite Faded Fantasy","Music",5,0,0,"N","Y","Five Stars","The best album ever!","2014-12-29"
"UK",10629,"R2K4BOL8MN1TTY","B006CHML4I",835010224,"Seiko 5 Men's Automatic Watch with Black Dial Analogue Display and Blue Fabric Strap SNK807K2","Watches",4,0,0,"N","Y","Great watch from casio.","What a great watch. Both watches and strap is in a great quality, and the prize is low. Especially compared to the price here in Denmark.","2013-10-24"
"UK",12136,"R3P40IEALROVCH","B00IIFCJX0",271687675,"Dexter Season 8","Digital_Video_Download",5,0,0,"N","Y","fantastic","love watching all the episodes of Dexter, when i first heard about this series i wasnt too sure about watching it. it took me a very long time to start and 

"UK",20583,"R28IKPKZMZZV52","B00A6HL704",438645704,"The Twilight Saga: The Complete Collection [DVD]","Video DVD",4,0,3,"N","Y","all good apart from postage","didn't turn up on time and paid extra for day of release. DVD fine just the timing was awful which ruined the experience.","2013-03-15"
"UK",20725,"R21DHG6AOGXIZ6","B00IABBXIO",777928797,"RATHER BE - CLEAN BANDIT","Music",5,0,1,"N","Y","Top tune","Bought this single as it was number 1 the day my daughter was born. Didn't like it at 1st but it's grown on me and now I love it. Great catchy tune.","2014-04-12"
"UK",20849,"R2Z32STUPPU8O4","B00FDPK2JQ",650376702,"Salute","Music",5,0,0,"N","Y","music","bought for son for christmas he loves  liitle mix just started listening to music after turning 12 yrs of age great for teenages","2014-01-07"
"UK",20849,"R2K985KNJXCYX0","B004B8NBQW",702526844,"Bright Lights","Music",5,0,0,"N","Y","amazing","bought for hubby for christmas great fan of ellie goulding love all of her music fast delivery i

<a id='check_db'></a>
### Checking the database state

Here, we'll go over 3 useful commands to check the state of database server. For details and syntax of each command, refer to man page. 

`ess server summary` provide overall information and status of the database server, such as database, table, vectors and its schema.

In [13]:
ess server summary

DATABASE : amazon (active)
   TABLE :reviews	S:marketplace I,pkey:customer_id S:review_id S:product_id I:product_parent S:product_title S:product_category I:star_rating I:helpful_votes I:total_votes S:vine S:verified_purchase S:review_headline S:review_body S:review_date
  VECTOR : (none)
     VAR : (none)

ip-10-10-1-118: (+) udbd-10010 (4114) running.


`udbd status` return if the server is running or not.

In [22]:
ess exec "udbd status"

ip-10-10-1-118: (+) udbd-10010 (4114) running.


`aq_udb`'s option `-inf` providee information about a specific database running on a server.

In [21]:
aq_udb -inf amazon

"memx","strx","pkey","var","reviews"
1335836544,4914141,1059156,0,1969910


<a id='clean_db'></a>
### Clean Up Dabase
Now we know how to create and get infomation about our ubd and server, let's learn how to clean it up after using it, based on user cases.


**1. Stop database server and delete schema**<br>
* `ess server reset`: use this when you're not planning on using the database and its schema again.
* New data schema needs to be created from scratch

**2. Stop the database server, but preserve schema**<br>
* `(ess) udbd stop`: perfect for when you'd like to shut off your instance, but would like to come back and use the database again. 
* To use it again, start the server with `ess udbd start` and fill it up with data.

**3. Clear up the data inside of database**<br>
* `aq_udb -clr`: empty the data from database, tables, etc. Use this to repopulate tables/whole database. 
    * with Table name, empty the data but preserves the DB and table schema
    * with database name, empty the whole database (not delete??), you can refill the data again without creating schema
            
            
On the following 3 cells, we'll demonstrate each commands, and output the results using `ess server summary`

In [39]:
# case 1, delete everything
ess server reset
ess server summary

ip-10-10-1-118: No running server detected.


In [43]:
# stop the database server, preserve schema
ess udbd stop
ess server summary

ip-10-10-1-118: Stopping udbd-10010 (5182).
ip-10-10-1-118: udbd-10010 stopped.
DATABASE : amazon (active)
   TABLE :reviews	S:marketplace I,pkey:customer_id S:review_id S:product_id I:product_parent S:product_title S:product_category I:star_rating I:helpful_votes I:total_votes S:vine S:verified_purchase S:review_headline S:review_body S:review_date
  VECTOR : (none)
     VAR : (none)

2019-11-15 01:40:54 ip-10-10-1-118 ess[5291]: !!!Warning!!! Error executing: udbd status 10010
2019-11-15 01:40:54 ip-10-10-1-118 ess[5291]: ***Error*** ip-10-10-1-118: (-) udbd-10010 not running.



: 1

In [46]:
# clean up the data only
aq_udb -clr amazon:reviews
# check if the table is filled with data
aq_udb -exp amazon:reviews 

"marketplace","customer_id","review_id","product_id","product_parent","product_title","product_category","star_rating","helpful_votes","total_votes","vine","verified_purchase","review_headline","review_body","review_date"


<a id='aq_udb_option'></a>
## aq_udb options

Now we'll take a look at each options of `aq_udb` command. Before going through this section, go over [preparing databas](#prep_db) section and make sure database is running and filled with data.

<a id='exp'></a>
### -exp

This option export the data from given `DatabaseName:TableName`, or if only `DatabaseName` is given, then it'll export the primary keys from database. <br>

This option is used with many other options in order to process the data.
Let's take a look.

In [12]:
# exporting the data from table (-top 20 limits the output to 20 records)
aq_udb -exp amazon:reviews -top 30

"marketplace","customer_id","review_id","product_id","product_parent","product_title","product_category","star_rating","helpful_votes","total_votes","vine","verified_purchase","review_headline","review_body","review_date"
"UK",10349,"R2YVNBBMXD8KVJ","B00MWK7BWG",307651059,"My Favourite Faded Fantasy","Music",5,0,0,"N","Y","Five Stars","The best album ever!","2014-12-29"
"UK",10629,"R2K4BOL8MN1TTY","B006CHML4I",835010224,"Seiko 5 Men's Automatic Watch with Black Dial Analogue Display and Blue Fabric Strap SNK807K2","Watches",4,0,0,"N","Y","Great watch from casio.","What a great watch. Both watches and strap is in a great quality, and the prize is low. Especially compared to the price here in Denmark.","2013-10-24"
"UK",12136,"R3P40IEALROVCH","B00IIFCJX0",271687675,"Dexter Season 8","Digital_Video_Download",5,0,0,"N","Y","fantastic","love watching all the episodes of Dexter, when i first heard about this series i wasnt too sure about watching it. it took me a very long time to start and 

"UK",20583,"R28IKPKZMZZV52","B00A6HL704",438645704,"The Twilight Saga: The Complete Collection [DVD]","Video DVD",4,0,3,"N","Y","all good apart from postage","didn't turn up on time and paid extra for day of release. DVD fine just the timing was awful which ruined the experience.","2013-03-15"
"UK",20725,"R21DHG6AOGXIZ6","B00IABBXIO",777928797,"RATHER BE - CLEAN BANDIT","Music",5,0,1,"N","Y","Top tune","Bought this single as it was number 1 the day my daughter was born. Didn't like it at 1st but it's grown on me and now I love it. Great catchy tune.","2014-04-12"
"UK",20849,"R2Z32STUPPU8O4","B00FDPK2JQ",650376702,"Salute","Music",5,0,0,"N","Y","music","bought for son for christmas he loves  liitle mix just started listening to music after turning 12 yrs of age great for teenages","2014-01-07"
"UK",20849,"R2K985KNJXCYX0","B004B8NBQW",702526844,"Bright Lights","Music",5,0,0,"N","Y","amazing","bought for hubby for christmas great fan of ellie goulding love all of her music fast delivery i

In [37]:
# now outputting primary keys only
aq_udb -exp amazon -top 10

"marketplace"
"UK"
"JP"


In [37]:
# now outputting primary keys only
aq_udb -exp amazon -top 10

"marketplace"
"UK"
"JP"


<a id='top'></a>
### -top

This option limits the number of outputs to given number. Or users can specify the range of records to output. Let's take a look.

In [92]:
# output onlly the top 5 records
aq_udb -exp amazon:reviews -c marketplace review_id -top 5

"marketplace","review_id"
"UK","R2YVNBBMXD8KVJ"
"UK","R1P16QCZR7RHM"
"UK","R75U5MUIZ9T0D"
"UK","R3GVFV7NPBFAFJ"
"UK","R21DHG6AOGXIZ6"


In [94]:
# output records from 3 ~ 8
aq_udb -exp amazon:reviews -c marketplace review_id -top 3:5

"marketplace","review_id"
"UK","R75U5MUIZ9T0D"
"UK","R3GVFV7NPBFAFJ"
"UK","R21DHG6AOGXIZ6"
"UK","R2Z32STUPPU8O4"
"UK","R2K985KNJXCYX0"


<a id='last'></a>
### -last

Same as `-top`, but for retrieving record from the bottom of the database.

In [95]:
aq_udb -exp amazon:reviews -c marketplace review_id -last 5

"marketplace","review_id"
"UK","R1MNP9B6P9NZJX"
"UK","RLYB814UIM74F"
"JP","R27OUW6Q4KD4M"
"JP","R1EP2I6ARAO8V7"
"JP","RDB0HV9RADHQM"


In [97]:
# range can be specified also
aq_udb -exp amazon:reviews -c marketplace review_id -last 3:5

"marketplace","review_id"
"UK","R2O80C6DILMYCN"
"UK","R30YISPMTGGOGF"
"UK","R1MNP9B6P9NZJX"
"UK","RLYB814UIM74F"
"JP","R27OUW6Q4KD4M"


<a id='lim_rec'></a>
### -lim_rec

Limit the export result to provided number of records approximately.

In [88]:
aq_udb -exp amazon:reviews -lim_rec 2

"marketplace","customer_id","review_id","product_id","product_parent","product_title","product_category","star_rating","helpful_votes","total_votes","vine","verified_purchase","review_headline","review_body","review_date"
"UK",10349,"R2YVNBBMXD8KVJ","B00MWK7BWG",307651059,"My Favourite Faded Fantasy","Music",5,0,0,"N","Y","Five Stars","The best album ever!","2014-12-29"
"UK",13070,"R1P16QCZR7RHM","B00004WMYB",530484605,"The Marshall Mathers LP","Music",1,1,7,"N","Y","scratches n a crack","im very disappointed in amazon, theyre startin 2 sell used albums in the new section, i ordered this new and it came with scratches and a crack, track 19 couldnt even play all the way, smh, amazon has got 2 do better","2013-07-30"


<a id='lim_key'></a>
### -lim_key

Limit the output result to approximately given number of unique keys.
Let's limit the output to 5 product categories.

In [102]:
aq_udb -exp amazon:reviews -c product_category review_id -lim_key 5

"product_category","review_id"
"Music","R2YVNBBMXD8KVJ"
"Music","R1P16QCZR7RHM"
"Music","R75U5MUIZ9T0D"
"Music","R3GVFV7NPBFAFJ"
"Music","R21DHG6AOGXIZ6"
"Music","R2Z32STUPPU8O4"
"Music","R2K985KNJXCYX0"
"Music","R2ALDZENJR98RP"
"Music","R2AT8BOXVL4Y93"
"Music","R314E6OA2SYWLU"
"Music","R33H9NS55TQNWE"
"Music","R1I8DZWXUE11H8"
"Music","R15ATBRE953J70"
"Music","R1MA61IE4QT5BM"
"Music","R33KF3J2N7BT1W"
"Music","RRCKYC599FEIS"
"Music","R1ZC22KHL0Q337"
"Music","R2IXUXKN5J8MV2"
"Music","R2HI7O31H8ZREJ"
"Music","R1WBM2SHR7422I"
"Music","R3HJLWMPKOP6J5"
"Music","R36S37EIRDC9XZ"
"Music","R1PAMEP9SLZ9QV"
"Music","R1REP7JIENHKY6"
"Music","R2M25VMCRNZ5DS"
"Music","ROHA6HMOWKZJG"
"Music","R1PDY6EUIKY7ZE"
"Music","RGMI5HQOLN3G8"
"Music","R11K0U7LZY8WU8"
"Music","RFXTW559VCAYB"
"Music","REZH011WSY07T"
"Music","R3MB8B8WF83RRX"
"Music","R3T3MP46QP1UFI"
"Music","R4TZRC8XV28LH"
"Music","RXN0JWT8P1UDT"
"Music","RE41TPZJV43SZ"
"Music","R35U0ZKX5H5JC1"
"Music","R2LPVYE2ZJ6QKE"
"Music","R14OWUQHJRBM8G"
"Mus

"Music","RPFIBEJLEPORO"
"Music","R1ELEG4JZZCAWA"
"Music","R3VXAZQBDQWHC3"
"Music","R19CT9LM92TUW0"
"Music","R395C2R49W8VLE"
"Music","R37HEMS74MRS64"
"Music","R2G16D5VUAL24T"
"Music","R3LVNS1VXQ0JR6"
"Music","R1X2QLM9852UIT"
"Music","RXZXOIJ6WDFYX"
"Music","R2MZS8T67RNAH8"
"Music","R1W877HTDU09VY"
"Music","R18PY59VIAP4UX"
"Music","R2C15JFMR05SI2"
"Music","R2ZGNZXRAO5III"
"Music","R1EPP1FUWSCYPR"
"Music","R1WULNIMEEV7KW"
"Music","R24VVMOMZGRI0M"
"Music","R2P1AGDVB2BJMU"
"Music","R2MIL6BEHXTFO9"
"Music","R2OPUT3CFFF1LD"
"Music","R2NTEBFIFAGS2U"
"Music","R29C8WC58K2MQE"
"Music","R2D82V2YOLV271"
"Music","R2O3QIGBOW3NU7"
"Music","R31IHYSVSNUS97"
"Music","RFMGDNQ1LX1LD"
"Music","R1DLU2U2SAWKSJ"
"Music","R2Y5NIN2JP3M8R"
"Music","R32BJKWYV4WPXL"
"Music","R1PNJTGERANS9W"
"Music","RXO1GXLST89C8"
"Music","R3RAVN8PB1TA52"
"Music","R2JGAQ2RNMF3MQ"
"Music","RLRIODI1FAT3J"
"Music","R19PGXM6PEJUO4"
"Music","R1FU7289DQGCOA"
"Music","R45CE0Y9GZHQB"
"Music","R3QZ2UWGFAK976"
"Music","R1HTQZBWR6SCHU"
"Music

"Music","R1A972YQDTML6F"
"Music","RCPNFSKTCRCPJ"
"Music","R2RMSPT6PPVEJV"
"Music","R1D7Z2GB2W1JFR"
"Music","RGYQAP9UIBGNO"
"Music","R1FIEQJ0Z9N80P"
"Music","R1G59VV5I4I13U"
"Music","R1OOWK9C3FEDKO"
"Music","R371AU4JYTADWR"
"Music","R243PR4YPTLFZX"
"Music","RD690BURT5WK3"
"Music","R3DYIQPT6LBVUV"
"Music","RDD5G8U0KS0V3"
"Music","R14OLU1E3DK4QW"
"Music","R1N2R08O5V22KF"
"Music","R3FDLRR8W85AL2"
"Music","RDUPEQBKLRXDQ"
"Music","R23KQBW9YMYPZN"
"Music","R3QIAMXLULZ9EP"
"Music","RY7U82M8LECNG"
"Music","R2GS5QRP0C47IU"
"Music","R2DY1FFU93FWY3"
"Music","RTUAAKPU6ZZKL"
"Music","R30O5UZS57EMTP"
"Music","R1W972LBWFWPSE"
"Music","R2ZMTUCLKEOWFN"
"Music","R1RZEACQEF8KTC"
"Music","R2XGTTCVHOLBS4"
"Music","R2DIKMXKPVJS0U"
"Music","RWHEBD71H6BFV"
"Music","R90ULS1IFC9QA"
"Music","R308MIJ584UJV7"
"Music","R26OAVN7OL2BMK"
"Music","RW64WRL0J0EYF"
"Music","R2LKMQOP8FZIK7"
"Music","R37BCOWJI9CK7N"
"Music","R88RF6WDOXUY3"
"Music","R20L3I4G71K99M"
"Music","RDQ3U92W7E4ZK"
"Music","R414IERNLB3TW"
"Music","R2U4

"Music","RAZTOL3I4KE7U"
"Music","R2OGTU9IYJWE3R"
"Music","RVDS1XRRZ8H9K"
"Music","R20IHC8TOU87WA"
"Music","R2R3LQFE8DQCF2"
"Music","R2I8KM9D6M1EEO"
"Music","R3JBFDIYMTGZTU"
"Music","R3MF38TR0KRAZB"
"Music","R3OKOYARMQ6EM8"
"Music","R2Z6MIEL6HMCCH"
"Music","R2H9A2ECNWEV9P"
"Music","R29V7B6IEWPIG9"
"Music","R2E66VW0M2849Y"
"Music","R22HJDROXWGPRL"
"Music","R13N388MCGZK1L"
"Music","R3769RWKVML408"
"Music","R7ZJQXIUSOQ7Q"
"Music","R3LDW29ZZQQ80"
"Music","R1F2UT3GP5KAKL"
"Music","R1DULQZOSUKY4B"
"Music","R2ZHHPPGV2SMFZ"
"Music","RX90U6F90OXNA"
"Music","R3H4GI7TJPQVCY"
"Music","R2Q07LDQ3X9VGD"
"Music","R18LGFFELB1JCS"
"Music","R1VZBMBNRPVPE7"
"Music","R2VFGNGH2PCQHZ"
"Music","R1PRDJJNIQ8C95"
"Music","RMOKP6US9OFDT"
"Music","R1ZPW0S983J7BG"
"Music","R3BWHPNAEV7OMJ"
"Music","R1Z02ET73UOY0P"
"Music","R1RKS8QWGXPS37"
"Music","RA3JLZLU2P5T2"
"Music","R12LRD2MH2JVWX"
"Music","RWUMZDFVMP1UJ"
"Music","R39C7QMLGO8FII"
"Music","R3RRQAG8XF05ET"
"Music","R1L2SCNG5PM52A"
"Music","R10PGMCBKGMCOW"
"Music",

"Music","R1FYLR5ABORAOW"
"Music","REF8A5X5YXA7B"
"Music","RJLFUT03FUW8S"
"Music","R2KVODBT9P7RBR"
"Music","R230QDHJNBEV9G"
"Music","R26E3N426LZ5X5"
"Music","R1VURAYT9M5OWJ"
"Music","R3SU49BF8G8MV7"
"Music","R9OJ6PMUJ07HB"
"Music","R2FPWCYREHBUCN"
"Music","R1M7J1TMERBCQF"
"Music","R1M46DKSV34DLK"
"Music","R2KMUNVFHEFZVJ"
"Music","R1Q3MYUF5XNL7X"
"Music","R2ZUCPPO37NAHO"
"Music","R21RQGY1AUGKJZ"
"Music","R146JJGLWEB7KL"
"Music","R2DFL23CYYOSGB"
"Music","RGEJN9L11HEDI"
"Music","R1V3WF0KCRU2LQ"
"Music","R1M5BMWP4IQYHQ"
"Music","R3FFZX6RAJRP53"
"Music","R2BSADD1750MON"
"Music","RPBB1PXDTXIBE"
"Music","RIZJA8XDXHVDQ"
"Music","R2FUH34GMNTDS9"
"Music","R2NQY6L8HA0IF9"
"Music","R1XOPJC6QDII04"
"Music","R1EPFTTGUKLAFL"
"Music","RTR4C7RPZC5JL"
"Music","R3M4O2ZXHYI1I2"
"Music","R20W13SYWXAZZB"
"Music","R103VWQ39B7GIZ"
"Music","RVFJJQ643S5KA"
"Music","R36R88B2LBE73U"
"Music","R1DIHTIZI6VBV9"
"Music","R2ST8GOJB9PUZ7"
"Music","R1QZFWU7KSWFI4"
"Music","R3KS0NZQ3JFKJY"
"Music","R19OB1D3D523J"
"Music","

...

"Digital_Ebook_Purchase","R1KTGBLI1Z8JQ8"
"Digital_Ebook_Purchase","RO34L3L0AVL3P"
"Digital_Ebook_Purchase","RTUJVICUBX6HW"
"Digital_Ebook_Purchase","R1ZGACPH2OJP1H"
"Digital_Ebook_Purchase","R1M9VSKA4Z4WS7"
"Digital_Ebook_Purchase","R6CRCE533K8WZ"
"Digital_Ebook_Purchase","R29IX3BWVBP1VC"
"Digital_Ebook_Purchase","R3V5IVGLALL982"
"Digital_Ebook_Purchase","R2UWNL9PSN4IJF"
"Digital_Ebook_Purchase","R2QFQMOJJ5M5Y2"
"Digital_Ebook_Purchase","R1VGM0TEURT4PV"
"Digital_Ebook_Purchase","R5SMD66JE38QD"
"Digital_Ebook_Purchase","R1PXC7HQTAYHTG"
"Digital_Ebook_Purchase","R3CJ8NMT9T31ZH"
"Digital_Ebook_Purchase","R1R217V2V14N81"
"Digital_Ebook_Purchase","R3Q33Q9E17KKIW"
"Digital_Ebook_Purchase","RTZSL38CBSTQ0"
"Digital_Ebook_Purchase","RXIQK398X9GD1"
"Digital_Ebook_Purchase","R3V8EKYAKCHFCT"
"Digital_Ebook_Purchase","R1XRA29FANNSJT"
"Digital_Ebook_Purchase","R2V812GWM09J92"
"Digital_Ebook_Purchase","R1CFQ1P3YPCRTE"
"Digital_Ebook_Purchase","R24VT9EQZKKJR5"
"Digital_Ebook_Purchase","R35HU0YOEV9R65

"Digital_Ebook_Purchase","RVQG3MA50ED1R"
"Digital_Ebook_Purchase","R2VQNU754OYDKG"
"Digital_Ebook_Purchase","R194I824EASOH9"
"Digital_Ebook_Purchase","R3AZON1MNA1FTE"
"Digital_Ebook_Purchase","R3CF77AYBBP0IO"
"Digital_Ebook_Purchase","RNQYS41FVXZVM"
"Digital_Ebook_Purchase","R2GFEA1Q2FOR0X"
"Digital_Ebook_Purchase","R149KFJYFLJRE5"
"Digital_Ebook_Purchase","R33QJ5GLGDX3H6"
"Digital_Ebook_Purchase","R3PMIHUI06Q23K"
"Digital_Ebook_Purchase","R2IXG538T8KS2C"
"Digital_Ebook_Purchase","RMK2JFA0K29EL"
"Digital_Ebook_Purchase","R12ICIA5X5LY2D"
"Digital_Ebook_Purchase","RL3GZA7WUDVJE"
"Digital_Ebook_Purchase","R1LYHNDFSYCYPN"
"Digital_Ebook_Purchase","R1B4BERUGUTDJT"
"Digital_Ebook_Purchase","R3BNS24D2TYIL7"
"Digital_Ebook_Purchase","RQM1UVIMZ4BDS"
"Digital_Ebook_Purchase","R123BCMQ4LQN49"
"Digital_Ebook_Purchase","R1CQFOSGY5IE9S"
"Digital_Ebook_Purchase","R3U0G3UF11P4TQ"
"Digital_Ebook_Purchase","R2AMHUTX7ZGSYZ"
"Digital_Ebook_Purchase","R2AQSDWN0MJ6D2"
"Digital_Ebook_Purchase","RPVU81JQCOS9P

"Digital_Ebook_Purchase","R3L3G1VLB2X21M"
"Digital_Ebook_Purchase","R58HVOCDKNU1Y"
"Digital_Ebook_Purchase","R13EUEZBXLRP5A"
"Digital_Ebook_Purchase","R1FPFF86W9BJPM"
"Digital_Ebook_Purchase","R184IU25BIG1WD"
"Digital_Ebook_Purchase","R2UA36I1JEC6JF"
"Digital_Ebook_Purchase","R1Q2IN3751WB0M"
"Digital_Ebook_Purchase","R19A2PNOWWT04H"
"Digital_Ebook_Purchase","R2EJTZNOQNHLFM"
"Digital_Ebook_Purchase","RTWXLROOST9ZJ"
"Digital_Ebook_Purchase","R3JFCNSN7GFI72"
"Digital_Ebook_Purchase","RLR1BWML9XZ34"
"Digital_Ebook_Purchase","R3IMOV4GTO70L1"
"Digital_Ebook_Purchase","R29TBSY28PFNAV"
"Digital_Ebook_Purchase","R3L3IDJSM65OJH"
"Digital_Ebook_Purchase","R1OVZ1565PIJ9R"
"Digital_Ebook_Purchase","RM5TDTWVES6R8"
"Digital_Ebook_Purchase","R2Y475OE3P2Z1R"
"Digital_Ebook_Purchase","R2JO8VTABB6XW6"
"Digital_Ebook_Purchase","R2ORS12LKJALF7"
"Digital_Ebook_Purchase","RE0AXC02XSX3U"
"Digital_Ebook_Purchase","R2BPBS05IEA50U"
"Digital_Ebook_Purchase","R2HJM0WT8QVRFW"
"Digital_Ebook_Purchase","R11AAERJL9FXE

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



"Digital_Ebook_Purchase","R2GVULUM5IMTNZ"
"Digital_Ebook_Purchase","R3SUPE91DZIONR"
"Digital_Ebook_Purchase","R30PJU6XNPE4EG"
"Digital_Ebook_Purchase","RDXCPIEX4RU2C"
"Digital_Ebook_Purchase","R21Y378DQZK84H"
"Digital_Ebook_Purchase","R14B106AYCFZZ4"
"Digital_Ebook_Purchase","R36F3VJ85DLTS"
"Digital_Ebook_Purchase","R3F9DHM3G4QFU2"
"Digital_Ebook_Purchase","R1LIFHTFZMFCDL"
"Digital_Ebook_Purchase","RL071YOJ2QLR2"
"Digital_Ebook_Purchase","R128V7U9B6YS2Q"
"Digital_Ebook_Purchase","R1JU7BYYMD4ZN3"
"Digital_Ebook_Purchase","R2V7D2T9AFN2P6"
"Digital_Ebook_Purchase","R3R6WXTW61209I"
"Digital_Ebook_Purchase","R372IFGSR00EY3"
"Digital_Ebook_Purchase","R3AIRTDF3LPER"
"Digital_Ebook_Purchase","R2QBAWV9TNG2LP"
"Digital_Ebook_Purchase","R1P0PYVJYBMXH8"
"Digital_Ebook_Purchase","R31CMJ21UUBQJU"
"Digital_Ebook_Purchase","R2MQ2KJAC70OTT"
"Digital_Ebook_Purchase","R1SBO4WKIOF46V"
"Digital_Ebook_Purchase","RCIFF9FN8936X"
"Digital_Ebook_Purchase","R6OOT69RO5DEL"
"Digital_Ebook_Purchase","R2D64CQBFJIJN"

<a id='key_rec'></a>
### -key_rec

Limit the output of `-exp` to a number of records per each uniuqe key value.

In this example will output 5 numbers of records per product category.

In [100]:
aq_udb -exp amazon:reviews -c product_category review_id -key_rec 5

"product_category","review_id"
"Music","R2YVNBBMXD8KVJ"
"Music","R1P16QCZR7RHM"
"Music","R75U5MUIZ9T0D"
"Music","R3GVFV7NPBFAFJ"
"Music","R21DHG6AOGXIZ6"
"Watches","R2K4BOL8MN1TTY"
"Watches","R1ONBLBRBW5IH8"
"Watches","R3C0KKBKGI8DX2"
"Watches","R2FEAD5Z8YWCDA"
"Watches","R2ERSR2PE6L4H8"
"Digital_Video_Download","R3P40IEALROVCH"
"Digital_Video_Download","RCLXN2CQ9AZFQ"
"Digital_Video_Download","RFRQX0KZKLIVG"
"Digital_Video_Download","RZ4X6LS13SLD6"
"Digital_Video_Download","R1YBG92V65P5CV"
"Toys","R25XL1WWYRDLA9"
"Toys","RN6TFJLG0LK08"
"Toys","R253TMIYVMIAIR"
"Toys","R27DCVPHY22QWG"
"Toys","R3GW05VQC6HV3Y"
"Digital_Ebook_Purchase","RVTVB9YDXSFYH"
"Digital_Ebook_Purchase","R3DHVC6SGQS5JU"
"Digital_Ebook_Purchase","R335F97BGBKXY7"
"Digital_Ebook_Purchase","R2N8VYUJNFZ5VV"
"Digital_Ebook_Purchase","R1PCZWZL16D206"
"Books","R2F2I7T03D42TE"
"Books","R39A5MVUEY58YJ"
"Books","R309H0D9CVW4OW"
"Books","R3TAKVKZETW923"
"Books","R1FU9OH1KFV7YF"
"Video DVD","R3G5WIW7NNA1CS"
"Video DVD","R2KXGMVFS

<a id='sort'></a>
### -sort

You can sort the data based on given column name, as it is being exported. Note that the records in the database is not sorted.


In [65]:
# sorting based on customer_id column. feel free to try other column as well.
# -c option is used to output given column only
aq_udb -exp amazon:reviews -sort customer_id -top 10 -c customer_id

"customer_id"
10349
10629
12136
12268
12677
13070
15356
16019
16563
17139


In [38]:
# note that this command does not change the order of data within the table
aq_udb -exp amazon:reviews -top 10 -c customer_id

"customer_id"
10349
10629
12136
12268
12677
13070
15356
16019
16563
17139


<a id='ord'></a>
### -ord

This option is different from usual sorting you'd encounter in 2 ways.
* sort the data internally (change the order of records within the database) and does not output the result
* sort the records within group of primary key (Groupby Primary key column, then sort) 

Note that **primary key is `product_category`**.

In [51]:
# sorting the records based on star_rating column (within same product category)
aq_udb -ord amazon:reviews star_rating

# display the result, 20 records per category only for clearity
aq_udb -exp amazon:reviews -c product_category star_rating -key_rec 20

"product_category","star_rating"
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video

"Software",1
"Software",1
"Software",1
"Software",1
"Software",1
"Software",1
"Software",2
"Software",2
"Software",2
"Software",2
"Software",2
"Software",2
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Pet Products",1
"Pet Products",1
"Pet Produ

In [52]:
# sort in decsending order as well
aq_udb -ord,dec amazon:reviews star_rating

aq_udb -exp amazon:reviews -c product_category star_rating -key_rec 20

"product_category","star_rating"
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video

"Software",5
"Software",5
"Software",5
"Software",5
"Software",5
"Software",5
"Software",5
"Software",5
"Software",5
"Software",5
"Software",5
"Software",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Pet Products",5
"Pet Products",5
"Pet Produ

<a id='shf'></a>
### -shf

This option shuffle the data internally by keys, so does not produce output. 
Let's check it out.


In [55]:
# First we will sort the data based on star_rating, and output the result 
aq_udb -ord amazon:reviews star_rating
# Output the first 20 records per category of sorted data
aq_udb -exp amazon:reviews -c product_category star_rating -key_rec 20

"product_category","star_rating"
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Music",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Watches",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video_Download",1
"Digital_Video

"Software",1
"Software",1
"Software",1
"Software",1
"Software",1
"Software",1
"Software",2
"Software",2
"Software",2
"Software",2
"Software",2
"Software",2
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Office Products",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",1
"Pet Products",1
"Pet Products",1
"Pet Produ

**Notice the record will be shuffled within each primary key group (product category)**.

In [61]:
# Now applying shuffling 
aq_udb -shf amazon:reviews

# output the result
# Output the first 20 records per category of sorted data
aq_udb -exp amazon:reviews -c product_category star_rating -key_rec 20

"product_category","star_rating"
"Music",5
"Music",4
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",4
"Music",3
"Music",5
"Music",4
"Music",3
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Music",5
"Watches",5
"Watches",2
"Watches",5
"Watches",4
"Watches",5
"Watches",4
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",4
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",5
"Watches",4
"Watches",5
"Watches",5
"Watches",5
"Digital_Video_Download",3
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",1
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",4
"Digital_Video_Download",2
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",4
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",2
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video_Download",5
"Digital_Video

"Software",5
"Software",4
"Software",4
"Software",2
"Software",5
"Software",1
"Software",5
"Software",5
"Software",5
"Software",5
"Software",5
"Software",4
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",4
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",3
"Office Products",5
"Office Products",5
"Office Products",4
"Office Products",5
"Office Products",5
"Office Products",1
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Office Products",5
"Lawn and Garden",4
"Lawn and Garden",4
"Lawn and Garden",5
"Lawn and Garden",1
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",3
"Lawn and Garden",4
"Lawn and Garden",4
"Lawn and Garden",2
"Lawn and Garden",5
"Lawn and Garden",5
"Lawn and Garden",1
"Lawn and Garden",2
"Lawn and Garden",5
"Lawn and Garden",1
"Lawn and Garden",1
"Lawn and Garden",2
"Lawn and Garden",3
"Pet Products",3
"Pet Products",4
"Pet Produ

<a id='cnt'></a>
### -cnt

Counts the numbers of primary keys in database, and if table/vector name is given also, it will outputs numbers of rows as well.

In this example, the primary key is set to `product_category`. So output will be the numbers of unique product category in the dataset.

In [66]:
# Counting numbers of primary keys only
aq_udb -cnt amazon

# counting primary keys and rows also, by providing table's name too
aq_udb -cnt amazon:reviews

"field","count"
"pkey",33
"field","count"
"pkey",33
"row",1969910


<a id='eval'></a>
### -eval

Same as the `-eval` option in `aq_pp` command, except that destination column must be either existing column or variable, and needs to be used with `-exp` option. <br>
Followings options are available as `Expr` as well.
* `aq_emod` functions
* Builtin Variables

In the example below, we'll provide `'star_rating * (-2)'` as expression and store the result in `arithmetic` column.

In [74]:
aq_udb -exp amazon:reviews -eval star_rating 'star_rating' -top 20 -c star_rating

<a id='filt'></a>
### -filt
Same as `-filt` option in `aq_pp` command. Let's take a look


In [77]:
# Filter the result by marketplace == Japan
aq_udb -exp amazon:reviews -filt 'marketplace == "JP"' -c marketplace review_headline -top 20

"marketplace","review_headline"
"JP","「90's Hip Hop 大名盤」、かつ、「90's 大名盤」！！！"
"JP","最高です"
"JP","昔からのファンの勝手な気持ちなぞ"
"JP","またいつか"
"JP","オーディオマニアにも聴いてほしい"
"JP","微妙です…"
"JP","価値の高いLiving Stereo SACDシリーズ"
"JP","でもさすが最強トリオです"
"JP","トビます , トビます ,"
"JP","何度も聴きまくってますｖ"
"JP","レコードの頃から"
"JP","特別なアルバム"
"JP","アールズコートという駅名をみて想う"
"JP","みくびってました。"
"JP","期待よりいまひとつ"
"JP","個人的にイングヴェイの最高作"
"JP","永久に循環するアルバム"
"JP","R・ウオーターズ抜きですが"
"JP","セカンドが楽しみ！"
"JP","デフ・レパードファンにオススメ"


<a id='var'></a>
### -var

Sets the value for predefined (at table creation stage with `ess create` command) variable.

A variable `star_sum` is defined. We will
1. store the cumulative sum in `star_sum`. 
2. divide it by the `rowNum` to get the temporary average star rating at the row
3. store that value in the star_rating column with `-eval` option.

**FIX THIS NOT WORKING**

In [84]:
aq_udb -exp amazon:reviews -var star_sum 'star_sum+star_rating' -eval star_rating 'star_sum' -top 20 -c star_rating

Server(127.0.0.1:10010) error: processing rule: Column "star_sum" not found

aq_udb: Udb request invalid


: 34